## Importing the libraries

In [1]:
import os
import pandas as pd
import numpy as np
import json
import spotipy
import spotipy.oauth2 as oauth2
from spotipy.oauth2 import SpotifyOAuth,SpotifyClientCredentials
import yaml
import re
from tqdm import tqdm
import multiprocessing as mp
import time
import random
import datetime

In [2]:
stream= open("spotify.yaml")
spotify_details = yaml.safe_load(stream)
auth_manager = SpotifyClientCredentials(client_id=spotify_details['Client_id'],
                                        client_secret=spotify_details['client_secret'])
sp = spotipy.client.Spotify(auth_manager=auth_manager)

## Importing the dataset

- Reading the 1 million playlists and keeping only the unique track URIs for the content-based recommendation system.
- The first for loop Read the 1,000 JSON files one at a time.
- The second for loop is for getting only the unique track.

In [3]:
def loop_slices(path, num_slices=20):
  cnt = 0
  cnt1 = 0
  mpd_playlists = []
  unique_tracks= pd.DataFrame()
  filenames = os.listdir(path)
  for fname in tqdm(sorted(filenames, key=len)):
    if fname.startswith("mpd.slice.") and fname.endswith(".json"):
      cnt += 1
      fullpath = os.sep.join((path, fname))
      f = open(fullpath)
      js = f.read()
      f.close()
      current_slice = json.loads(js)
      # Create a list of all playlists
      for playlist in current_slice['playlists']:
        cnt1 +=1
        mpd_playlists.append(playlist)
        if cnt1 == 1000:
          cnt1=0
          temp=pd.DataFrame(mpd_playlists)
          temp=temp.explode('tracks')
          temp=pd.DataFrame(temp['tracks'].apply(pd.Series))
          unique_tracks=pd.concat([unique_tracks,temp],axis=0)
          unique_tracks.drop_duplicates(subset=['track_uri'],inplace=True)
          mpd_playlists = []
      if cnt == num_slices:
        break
  return unique_tracks
# Path where the json files are extracted
path = 'C:/Users/steve/OneDrive/Pictures/spotify_million_playlist_dataset/data'

In [3]:
df = pd.read_csv('C:/Users/steve/SpotifyGenie/CSE5914-SpotifyGroup/spotify-genie/Datasets/neededsongs.csv')

In [4]:
df["track_uri"] = df["track_uri"].apply(lambda x: re.findall(r'\w+$', x)[0])
df["artist_uri"] = df["artist_uri"].apply(lambda x: re.findall(r'\w+$', x)[0])
df["album_uri"] = df["album_uri"].apply(lambda x: re.findall(r'\w+$', x)[0])

In [5]:
df = df[['track_uri', 'artist_uri', 'album_uri']]

In [6]:
t_uri=df["track_uri"].unique()
a_uri=df["artist_uri"].unique()

In [7]:
print(len(a_uri))

192906


# Feature extraction

Using the Spotify API for Feature Extraction and Saving Results to a CSV File and Errors to a Log File

I was using SP.track first, but I realised that it would take a lot of time and I would have to counter a lot of Api rate limits, so I used SP.tracks and SP.artists instead. They accept lists with a 50-URI maximum and handle them in a single request, so it took a lot less time.

In [8]:
print(len(t_uri))

952763


In [9]:
f = open('C:/Users/steve/SpotifyGenie/CSE5914-SpotifyGroup/spotify-genie/Datasets/track_features.csv','a')

e=0
for i in tqdm(range(0,len(t_uri),50)):
    try:
        track_features = sp.tracks(t_uri[i:i+50])
        for x in range(50):
            track_pop=pd.DataFrame([t_uri[i+x]])
            track_pop['release_date']=track_features['tracks'][x]['album']['release_date']
            track_pop['pop'] = track_features['tracks'][x]["popularity"]
            csv_data = track_pop.to_csv(header=False,index=False)
            f.write(csv_data)
    except Exception as error:
        e+=1
        r = open("track_features.txt", "a")
        r.write(datetime.datetime.now().strftime("%d.%b %Y %H:%M:%S")+": "+str(error)+'\n')
        r.close()
        continue
r = open("track_features.txt", "a")
r.write(datetime.datetime.now().strftime("%d.%b %Y %H:%M:%S")+" _________________________ "+"Total Number Of Errors : "+str(e)+" _________________________ "+'\n')
r.close()
f.close()

  0%|          | 0/19056 [00:00<?, ?it/s]

  0%|          | 1/19056 [00:00<2:40:13,  1.98it/s]

In [20]:
import time
import datetime
import pandas as pd
from tqdm import tqdm

# Define the initial waiting time (in seconds)
initial_wait_time = 1

# Function to perform exponential backoff
def exponential_backoff(retries):
    return initial_wait_time * 2 ** retries

# Open the file for writing data
f = open('C:/Users/steve/OneDrive/Pictures/spotify_million_playlist_dataset/data/audio_features.csv','a')

# Initialize error counter
e = 0

# Loop through the track URIs in batches of 100
for i in tqdm(range(int(len(t_uri)/2) + 250000, len(t_uri),100)):
    retries = 0
    while True:
        try:
            time.sleep(1)
            # Query Spotify API for audio features
            track_feature = sp.audio_features(t_uri[i:i+10])
            track_df = pd.DataFrame(track_feature)
            csv_data = track_df.to_csv(header=False, index=False)
            f.write(csv_data)
            break  # Break out of the retry loop if successful
        except Exception as error:
            print(i)
            print(error)
            i += 1
            e += 1
            r = open("audio_features_log.txt", "a")
            r.write(datetime.datetime.now().strftime("%d.%b %Y %H:%M:%S") + ": " + str(error) + '\n')
            r.close()
            # Calculate the backoff time
            retries += 1

# Write total number of errors to the log file
r = open("audio_features_log.txt", "a")
r.write(datetime.datetime.now().strftime("%d.%b %Y %H:%M:%S") + " _________________________ " + "Total Number Of Errors : " + str(e) + " _________________________ " + '\n')
r.close()

# Close the files.
f.close()


  0%|          | 0/8812 [00:01<?, ?it/s]


KeyboardInterrupt: 

In [9]:

f = open('C:/Users/steve/OneDrive/Pictures/spotify_million_playlist_dataset/data/artist_features.csv','a')
e=0

In [15]:

for i in tqdm(range(0,len(a_uri),50)):  
    try:
        artist_features = sp.artists(a_uri[i:i+50])
        for x in range(50):
            artist_df=pd.DataFrame([a_uri[i+x]])
            artist_pop = artist_features['artists'][x]["popularity"]
            artist_genres = artist_features['artists'][x]["genres"]
            artist_df["artist_pop"] = artist_pop
            if artist_genres: 
                artist_df["genres"] = " ".join([re.sub(' ','_',i) for i in artist_genres])
            else:
              artist_df["genres"] = "unknown"
            csv_data = artist_df.to_csv(header=False,index=False)
            f.write(csv_data)
    except Exception as error:
        e+=1
        r = open("artist_features.txt", "a")
        r.write(datetime.datetime.now().strftime("%d.%b %Y %H:%M:%S")+": "+str(error)+'\n')
        r.close()
        time.sleep(3)
        continue
r = open("artist_features.txt", "a")
r.write(datetime.datetime.now().strftime("%d.%b %Y %H:%M:%S")+" _________________________ "+"Total Number Of Errors : "+str(e)+" _________________________ "+'\n')
r.close()
f.close()

  0%|          | 0/5918 [00:00<?, ?it/s]

['2wIVse2owClT7go1WT98tk', '26dSoYclwsYLMAKD3tpOr4', '6vWDO969PvNqNYHIOW5v0m', '31TPClRtHm23RisEBtV3X7', '5EvFsr3kj42KNv97ZEnqij', '23zg3TcAtWQy7J6upgbUnj', '6wPhSqRtPu1UhRCDX5yaDJ', '1Y8cdNmUJH7yBTd9yOvr5i', '1G9G7WwrXka3Z1r7aIDjI7', '2jw70GZXlAI8QzWeY2bgRc', '2Hjj68yyUPiC0HKEOigcEp', '27FGXRNruFoOdf1vP8dqcH', '0f5nVCcR06GX8Qikz0COtT', '0p4nmQO2msCgU4IF37Wi3j', '7bXgB6jMjp9ATFy66eO08Z', '4TKTii6gnOnUXQHyuo9JaD', '1yxSLGMDHlW21z4YXirZDS', '5ND0mGcL9SKSjWIjPd0xIb', '01lz5VBfkMFDteSA9pKJuP', '7gOdHgIoIKoe4i9Tta6qdD', '5qK5bOC6wLtuLhG5KvU17c', '0N0d3kjwdY2h7UVuTdJGfp', '07YZf4WDAMNwqr4jfgOZ8y', '21E3waRsmPlU7jZsS13rcj', '5YGY8feqx7naU7z4HrwZM6', '0vWCyXMrrvMlCcepuOJaGI', '5tKXB9uuebKE34yowVaU3C', '6LqNN22kT3074XbTVUrhzX', '1uNFoZAHBGtllmzznpCI3s', '0QJIPDAEDILuo8AIq3pMuU', '0C0XlULifJtAgn6ZNCW2eu', '6FBDaR13swtiWwGhX1WQsP', '3vAaWhdBR38Q02ohXqaNHT', '5ILrArfIV0tMURcHJN8Q07', '7vWBZm3sQ8yQvfV4nXxHXK', '6S2OmqARrzebs0tKUEyXyp', '3ao3jf5d70Tf4fPh2bnXVl', '26bcq2nyj5GB7uRr558iQg', '7zdmbPudNX

  0%|          | 1/5918 [00:00<40:47,  2.42it/s]

['29kkCKKGXheHuoO829FxWK', '0PFtn5NtBbbUNbU9EAmIWF', '2hl0xAkS2AIRAu23TVMBG1', '1dfeR4HaWDbWqFHLkxsg1d', '3qm84nBOXUEQ2vnTfUTTFC', '3IYUhFvPQItj6xySrBmZkd', '27T030eWyCQRmDyuvr1kxY', '2Hkut4rAAyrQxRdof7FVJq', '7lXgbtBDcCRbfc5f8FhGUL', '2e4G04F77jxVuDYo44TCSm', '0hT0UrjmzkLJouAT52ck6j', '3Nrfpe0tUJi4K4DXYWgMUX', '3g34PW5oNmDBxMVUTzx2XK', '7cVZApDoQZpS447nHTsNqu', '3uGFTJ7JMllvhgGpumieHF', '1ukccHTdm6Xjmag0QLNJBx', '5HenzRvMtSrgtvU16XAoby', '2JhAlkmukNvarUpGhTFXUQ', '31oLAWK0QuX1XLh6FmlTye', '4XDi67ZENZcbfKnvMnTYsI', '4XpUIb8uuNlIWVKmgKZXC0', '41MozSoPIsD1dJM0CLPjZF', '1sVSMPPNMMSZ7cQNfbvMOe', '6zhAP0FoDccL9kuETOC20q', '6dCz3spfpIvqqqsIoP6wXi', '2uWcrwgWmZcQc3IPBs3tfU', '4U80LJd8sG6U9YTFP5izka', '4ufh0WuMZh6y4Dmdnklvdl', '3JsHnjpbhX4SnySpvpa9DK', '4Kxlr1PRlDKEB0ekOCyHgX', '30b9WulBM8sFuBo17nNq9c', '7F3F1w0FK3HYyNLe3wE56T', '6udveWUgX4vu75FF0DTrXV', '6OwKE9Ez6ALxpTaKcT5ayv', '3cjEqqelV9zb4BYE3qDQ4O', '3UwlejyX2b458azZ7eCnHb', '05uheFGPahVh2nHIZK1KuB', '6LPOT9C3gvGQHxlZtMLHHg', '0bxSJJ7V2M

  0%|          | 3/5918 [00:00<25:26,  3.87it/s]

...

['4TFrKZqLFTm58aZpf6mSXB', '0pseAmAv5QD9T8dVVaOtiD', '6g9PeDHg982hw1WlGtZwC3', '5s7hqGPeEbPdHeThyBoeJd', '1gGbyGTnHVTCvi6uMOdkUZ', '7CXgiYtZiPnwxHM8ad4hNZ', '6j7ATeiPpRxLHrrqhgitlV', '58nhaWrZa0dN2OxZ1Pr2Ph', '2WndMx6hcSsypTze6YrPUp', '34RFQ2s5ENhZayvrHa9rpG', '4I5e89tBU2VPLQb10i0ZOC', '1Kv1eRA7iOeYWbJwZUfw1v', '1VlIssOVvlK9MhmkVbZRjN', '6ETbBkDMf7Kt9hBtESmuKY', '7gdDZhNP6HrfV6S3R4rR9r', '501nvyCBagmy5XueDn7X0C', '0hiIdy6vvtQmm4XvDs8sDg', '5MK48A9b19ltcMzWU9YJNr', '6ddN4xGSzJ78FAgdljlVsx', '0bZcAmkMLSVqFs4eE3sNNk', '2etWSM1cPeITq5E2bEK8PW', '3eJCIS7ytlYvT3pgReuWWa', '2sJ85ckVNzF8WoK0g5HbNX', '15kP9gcsrXB6gMYS7fyWWp', '2LHVIkOIGHS49rA0HAs6yi', '4mW0ptrT2j55Q2Q6taaPa0', '06T4DSqKYfs3ImrnzlIdeN', '59yfJA3UvWXUAFUbZFLQXS', '5zkhOMIQEsnM3MjwzXAOWu', '2QH3BeaAfy5fEmXu9DPriV', '4wR4mVx5q3hJuM7ad60N7s', '7g3jOiJLcyH5GIOVh6vfXm', '2794rI2eXBbA0ACxzveR0c', '0ucB95IfAINKSC7VYyF9Tn', '3IB8MySfR2EBMeLxC3oVx9', '53zPVFS5lrh8IAwsr7JdL1', '5CipVQH0CxeeBspFZkYMfF', '2Fi0a9OJGrQAcvbeRtJfV3', '2OTk1WFYoW

 84%|████████▎ | 4945/5918 [18:06<03:07,  5.18it/s]

['3JdmbSa6xA2hOvl9YERRb7', '0K3OmjqX9X55BCgGoa2WcD', '5XyCx0IBomTCtoqmOdSpmK', '4uGlaZn0LSybHkHFEKBOV2', '0nKXjn7KwxiinYESLbMK7U', '1ga9b9ldU5OjOeFx7v5sHH', '3HST6KDaE31eQCB5PE6qc8', '6Mpfs0gPZ1OumEoZMjr6vt', '7GlRfDEhsUyHv1CI3dQPpL', '6zxsn8XiVwz1Xs6uUvJ45U', '5gGzQgygoCuJtht0pWG7Uk', '52QgzwyRpxKpLW1baJPaSx', '2IcFCj6c6iRJQhXhNGu6dT', '5gNNwilt2CvTk0DVAISOze', '1A0LNR9Im28jKgI0QPCwJP', '60KXO0AGG9UCaQxv0lN0ZC', '1qkcrWj5Ko6RxcrRgWRNTY', '2cUbZ5W1iJYQQaviCOS1XM', '2bAAi9PF1xnI97J0x24BaM', '1YejgOhBY0bJ3MlYJ5JFac', '04bDWf1u7HxKdskC3N2nIk', '3RGF93b8Qtz77GLJBgdBH6', '0bs1y68FycnwnGpY15MoCT', '1Asm5ItmOMIeipn37o6wUf', '0sUnlzdWBhVAb46Bmv39iN', '4KtHTrxeTEhU1tJ0sIZh7U', '770jbmsPC0Wahj4gqfCkmr', '4Wpyd7QvaypDQ2tjhlecgh', '6K7g8yTt8T5IZzsW2fd824', '6pD8Xt0gBCh1jh7cVZj9vi', '2jwAs7CRbywfGPKX9IUVS5', '3oPXkGl9FuO3vnuwDYV1RT', '1cpfEmXLpGKjOx9LukhRKv', '0YjjkaGJ3NdzzYGbmBy4bU', '547lYuO3MeDrmZjHwlBzH1', '3eG4O7fVoq3zenBcZqjbf7', '52FLM766AqjFQKdOVUpGv7', '0h4zq4tFFGhKOamG1FzbOl', '1FCJcrr0GY

 84%|████████▎ | 4947/5918 [18:06<03:03,  5.28it/s]

['5tL6ZEc1OD4kIGlRHByWrv', '0wxx3VpAq4mTlN3mel0QvG', '6nb6Lt8SpJuLhE7jDl95aF', '7KAOkHGHCdP6nFGNC3eM15', '6l4Hexgj62gCu3oy7zfBrx', '5gEJrsghldz63fDxu1XqHA', '472UiuTOCqJX7KFvIBUbij', '3nasa4yabzvUeb6DzejDYU', '410n3dpwkfGswGSu4wnXgM', '59Zt62hHpwOfiTC918y1bQ', '7jLBNO5NZWjJO8f27wBvq0', '1Lvq7g5aUB3sjNhaWhoTor', '2Z6Cx9EVI8Sd47QNH8yDba', '3KSK3XBEY3070d0T7gbF6J', '1VxfKl0Gxn4bbutplSbEdS', '130A1NENzgUPKyAnjpmEqW', '5TCSgWFB2zp9SGYclb4VNT', '0MShkn0tHaqdmyjUrdMtV3', '0OZ3JC2i8oqafR5MpOA3QW', '1dXdQ2jWZwBdojaAiLjyIc', '38HFp5OVCJTRO3GqFiOKdr', '4GmkYQbOS7mjZcNBIKdzjz', '2RL6Xr1AbrHc6MtIIkuAlZ', '4AMpFkpUhQQOTaQOkXiHwg', '0SxKBjlxP5eEq3sUSsZnED', '4ztakVdT3nUD6FxF3Omm21', '3dQ7Pqoe915voh6dLHO5Os', '0fWoq3kKL2bsVmRYbDD91U', '0uBFx9AIFMgWSEwAyGKrp3', '00UMLCX51uNiBzMhQKlwyQ', '6Evthx116K8vsZKghwceoh', '2809MNtibD9ihJq1Hp3XUX', '5TWdMWG5VY8Im9RLUKwlfx', '3BCehx9UyxHIFrEl3PfOTp', '0D4soVdRj8gmbnDFKqOY5G', '2QgRf8bbA6wyuGiQ8hbBee', '6ok7jbEUCX0Q5S7eAsIur1', '0ULJLG31nDfJLdRS4wy6I5', '2qEhAz6MYv